In [1]:
import pandas as pd
import numpy as np

In [2]:
df=pd.read_csv("/kaggle/input/icr-identify-age-related-conditions/train.csv")
val=pd.read_csv("/kaggle/input/icr-identify-age-related-conditions/test.csv")
sub=pd.read_csv("/kaggle/input/icr-identify-age-related-conditions/sample_submission.csv")

In [3]:
#zero, one =np.bincount(df['Class'])

In [4]:
#zero_df=df.loc[df['Class']==0]
#one_df=df.loc[df['Class']==1]

In [5]:
#zero_df=zero_df.dropna()
#zero_df.shape

In [6]:
#one_df=one_df.fillna(df.median(numeric_only=True))
#zero_df=zero_df.fillna(df.median(numeric_only=True))

In [7]:
#zero_df=zero_df.drop(zero_df.sample(106).index)

In [8]:
#zero_df.shape

In [9]:
#data=pd.concat([one_df,zero_df])

In [10]:
##data=data.sample(frac=1,random_state=42)
#data = data.reset_index(drop=True)

data=df
data=data.fillna(data.median())

/tmp/ipykernel_20/4216217078.py:5: FutureWarning: The default value of numeric_only in DataFrame.median is deprecated. In a future version, it will default to False. In addition, specifying 'numeric_only=None' is deprecated. Select only valid columns or specify the value of numeric_only to silence this warning.
  data=data.fillna(data.median())


In [11]:
from sklearn.preprocessing import LabelEncoder

data['EJ'] = LabelEncoder().fit_transform(data['EJ'])
data=data.drop(['Id'], axis=1)

/opt/conda/lib/python3.10/site-packages/scipy/__init__.py:146: UserWarning: A NumPy version >=1.16.5 and <1.23.0 is required for this version of SciPy (detected version 1.23.5
  warnings.warn(f"A NumPy version >={np_minversion} and <{np_maxversion}"


In [12]:
val['EJ']=LabelEncoder().fit_transform(val['EJ'])
val=val.drop(['Id'], axis=1)

In [13]:
def competition_log_loss(y_pred, y_true):
    # y_true: correct labels 0, 1
    # y_pred: predicted probabilities of class=1
    #y_pred = y_pred.T[1]
    N_0 = np.sum(1 - y_true)
    N_1 = np.sum(y_true)
    w_0 = (N_0 + N_1) / N_0
    w_1 = (N_0 + N_1) / N_1
    # Calculate the predicted probabilities for each class
    p_1 = np.clip(y_pred, 1e-15, 1 - 1e-15)
    p_0 = 1 - p_1
    # Calculate the average log loss for each class
    sum_0 = -np.sum((1 - y_true) * np.log(p_0))
    sum_1 = -np.sum(y_true * np.log(p_1))
    to_output = ((w_0 / N_0) * sum_0 + (w_1 / N_1) * sum_1) / (w_0 + w_1)

    return to_output

In [14]:
X=data.drop(["Class"], axis=1)
y=data["Class"]

In [15]:
import lightgbm as lgbm
import optuna  # pip install optuna
from sklearn.metrics import log_loss
from sklearn.model_selection import StratifiedKFold
from optuna.integration import LightGBMPruningCallback

def objective(trial, X, y):
    param_grid = {
        # "device_type": trial.suggest_categorical("device_type", ['gpu']),
        "n_estimators": trial.suggest_categorical("n_estimators", [1000]),
        "learning_rate": trial.suggest_float("learning_rate", 0.1, 3.0),
        "num_leaves": trial.suggest_int("num_leaves", 20, 3000, step=20),
        "max_depth": trial.suggest_int("max_depth", 3, 12),
        #"min_data_in_leaf": trial.suggest_int("min_data_in_leaf", 1, 1000, step=20),
        "lambda_l1": trial.suggest_int("lambda_l1", 0, 25, step=5),
        "lambda_l2": trial.suggest_int("lambda_l2", 0, 25, step=5),
        #"min_gain_to_split": trial.suggest_float("min_gain_to_split", 0, 15),
        "bagging_fraction": trial.suggest_float(
            "bagging_fraction", 0.2, 0.95, step=0.1
        ),
        "bagging_freq": trial.suggest_categorical("bagging_freq", [1]),
        #"feature_fraction": trial.suggest_float(
         #   "feature_fraction", 0.2, 1, step=0.1
        #),
    }

    cv = StratifiedKFold(n_splits=5, shuffle=True, random_state=1121218)

    cv_scores = np.empty(5)
    for idx, (train_idx, test_idx) in enumerate(cv.split(X, y)):
        X_train, X_test = X.iloc[train_idx], X.iloc[test_idx]
        y_train, y_test = y[train_idx], y[test_idx]

        model = lgbm.LGBMClassifier(objective="binary", **param_grid)
        model.fit(
            X_train,
            y_train,
            eval_set=[(X_test, y_test)],
            eval_metric="binary_logloss",
            #custom_metric=competition_log_loss,
            early_stopping_rounds=100,
            callbacks=[
                LightGBMPruningCallback(trial, "binary_logloss")
            ],  # Add a pruning callback
        )
        preds = model.predict_proba(X_test)[:,1]
        cv_scores[idx] = competition_log_loss(preds, y_test)

    return np.mean(cv_scores)

In [16]:

study = optuna.create_study(direction="minimize", study_name="LGBM Classifier")
func = lambda trial: objective(trial, X, y)
study.optimize(func, n_trials=200)

[I 2023-07-29 09:48:15,845] A new study created in memory with name: LGBM Classifier
/opt/conda/lib/python3.10/site-packages/optuna/distributions.py:685: UserWarning: The distribution is specified by [0.2, 0.95] and step=0.1, but the range is not divisible by `step`. It will be replaced by [0.2, 0.9].
  warnings.warn(
/opt/conda/lib/python3.10/site-packages/lightgbm/sklearn.py:726: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/opt/conda/lib/python3.10/site-packages/lightgbm/sklearn.py:726: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will 

[LightGBM] [Warning] lambda_l1 is set=25, reg_alpha=0.0 will be ignored. Current value: lambda_l1=25
[LightGBM] [Warning] bagging_freq is set=1, subsample_freq=0 will be ignored. Current value: bagging_freq=1
[LightGBM] [Warning] lambda_l2 is set=0, reg_lambda=0.0 will be ignored. Current value: lambda_l2=0
[LightGBM] [Warning] bagging_fraction is set=0.5, subsample=1.0 will be ignored. Current value: bagging_fraction=0.5
[LightGBM] [Warning] lambda_l1 is set=25, reg_alpha=0.0 will be ignored. Current value: lambda_l1=25
[LightGBM] [Warning] bagging_freq is set=1, subsample_freq=0 will be ignored. Current value: bagging_freq=1
[LightGBM] [Warning] lambda_l2 is set=0, reg_lambda=0.0 will be ignored. Current value: lambda_l2=0
[LightGBM] [Warning] bagging_fraction is set=0.5, subsample=1.0 will be ignored. Current value: bagging_fraction=0.5


/opt/conda/lib/python3.10/site-packages/optuna/trial/_trial.py:494: UserWarning: The reported value is ignored because this `step` 0 is already reported.
  warnings.warn(
/opt/conda/lib/python3.10/site-packages/optuna/trial/_trial.py:494: UserWarning: The reported value is ignored because this `step` 1 is already reported.
  warnings.warn(
/opt/conda/lib/python3.10/site-packages/optuna/trial/_trial.py:494: UserWarning: The reported value is ignored because this `step` 2 is already reported.
  warnings.warn(
/opt/conda/lib/python3.10/site-packages/optuna/trial/_trial.py:494: UserWarning: The reported value is ignored because this `step` 3 is already reported.
  warnings.warn(
/opt/conda/lib/python3.10/site-packages/optuna/trial/_trial.py:494: UserWarning: The reported value is ignored because this `step` 4 is already reported.
  warnings.warn(
/opt/conda/lib/python3.10/site-packages/optuna/trial/_trial.py:494: UserWarning: The reported value is ignored because this `step` 5 is already r

[LightGBM] [Warning] lambda_l1 is set=25, reg_alpha=0.0 will be ignored. Current value: lambda_l1=25
[LightGBM] [Warning] bagging_freq is set=1, subsample_freq=0 will be ignored. Current value: bagging_freq=1
[LightGBM] [Warning] lambda_l2 is set=0, reg_lambda=0.0 will be ignored. Current value: lambda_l2=0
[LightGBM] [Warning] bagging_fraction is set=0.5, subsample=1.0 will be ignored. Current value: bagging_fraction=0.5


/opt/conda/lib/python3.10/site-packages/optuna/trial/_trial.py:494: UserWarning: The reported value is ignored because this `step` 67 is already reported.
  warnings.warn(
/opt/conda/lib/python3.10/site-packages/optuna/trial/_trial.py:494: UserWarning: The reported value is ignored because this `step` 68 is already reported.
  warnings.warn(
/opt/conda/lib/python3.10/site-packages/optuna/trial/_trial.py:494: UserWarning: The reported value is ignored because this `step` 69 is already reported.
  warnings.warn(
/opt/conda/lib/python3.10/site-packages/optuna/trial/_trial.py:494: UserWarning: The reported value is ignored because this `step` 70 is already reported.
  warnings.warn(
/opt/conda/lib/python3.10/site-packages/optuna/trial/_trial.py:494: UserWarning: The reported value is ignored because this `step` 71 is already reported.
  warnings.warn(
/opt/conda/lib/python3.10/site-packages/optuna/trial/_trial.py:494: UserWarning: The reported value is ignored because this `step` 72 is alr

...

/opt/conda/lib/python3.10/site-packages/optuna/trial/_trial.py:494: UserWarning: The reported value is ignored because this `step` 52 is already reported.
  warnings.warn(
/opt/conda/lib/python3.10/site-packages/optuna/trial/_trial.py:494: UserWarning: The reported value is ignored because this `step` 53 is already reported.
  warnings.warn(
/opt/conda/lib/python3.10/site-packages/optuna/trial/_trial.py:494: UserWarning: The reported value is ignored because this `step` 54 is already reported.
  warnings.warn(
/opt/conda/lib/python3.10/site-packages/optuna/trial/_trial.py:494: UserWarning: The reported value is ignored because this `step` 55 is already reported.
  warnings.warn(
/opt/conda/lib/python3.10/site-packages/optuna/trial/_trial.py:494: UserWarning: The reported value is ignored because this `step` 56 is already reported.
  warnings.warn(
/opt/conda/lib/python3.10/site-packages/optuna/trial/_trial.py:494: UserWarning: The reported value is ignored because this `step` 57 is alr

[LightGBM] [Warning] lambda_l1 is set=0, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0
[LightGBM] [Warning] bagging_freq is set=1, subsample_freq=0 will be ignored. Current value: bagging_freq=1
[LightGBM] [Warning] lambda_l2 is set=20, reg_lambda=0.0 will be ignored. Current value: lambda_l2=20
[LightGBM] [Warning] bagging_fraction is set=0.5, subsample=1.0 will be ignored. Current value: bagging_fraction=0.5


/opt/conda/lib/python3.10/site-packages/optuna/trial/_trial.py:494: UserWarning: The reported value is ignored because this `step` 22 is already reported.
  warnings.warn(
/opt/conda/lib/python3.10/site-packages/optuna/trial/_trial.py:494: UserWarning: The reported value is ignored because this `step` 23 is already reported.
  warnings.warn(
/opt/conda/lib/python3.10/site-packages/optuna/trial/_trial.py:494: UserWarning: The reported value is ignored because this `step` 24 is already reported.
  warnings.warn(
/opt/conda/lib/python3.10/site-packages/optuna/trial/_trial.py:494: UserWarning: The reported value is ignored because this `step` 25 is already reported.
  warnings.warn(
/opt/conda/lib/python3.10/site-packages/optuna/trial/_trial.py:494: UserWarning: The reported value is ignored because this `step` 26 is already reported.
  warnings.warn(
/opt/conda/lib/python3.10/site-packages/optuna/trial/_trial.py:494: UserWarning: The reported value is ignored because this `step` 27 is alr

[LightGBM] [Warning] lambda_l1 is set=0, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0
[LightGBM] [Warning] bagging_freq is set=1, subsample_freq=0 will be ignored. Current value: bagging_freq=1
[LightGBM] [Warning] lambda_l2 is set=20, reg_lambda=0.0 will be ignored. Current value: lambda_l2=20
[LightGBM] [Warning] bagging_fraction is set=0.5, subsample=1.0 will be ignored. Current value: bagging_fraction=0.5


/opt/conda/lib/python3.10/site-packages/optuna/distributions.py:685: UserWarning: The distribution is specified by [0.2, 0.95] and step=0.1, but the range is not divisible by `step`. It will be replaced by [0.2, 0.9].
  warnings.warn(
/opt/conda/lib/python3.10/site-packages/lightgbm/sklearn.py:726: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
[I 2023-07-29 09:50:59,757] Trial 194 pruned. Trial was pruned at iteration 2.
/opt/conda/lib/python3.10/site-packages/optuna/distributions.py:685: UserWarning: The distribution is specified by [0.2, 0.95] and step=0.1, but the range is not divisible by `step`. It will be replaced by [0.2, 0.9].
  warnings.warn(
/opt/conda/lib/python3.10/site-packages/lightgbm/sklearn.py:726: UserWarning: 'early_sto

In [17]:
print(f"\tBest value : {study.best_value}")
print(f"\tBest params:")

for key, value in study.best_params.items():
    print(f"\t\t{key}: {value}")

	Best value : 0.6212012399872412
	Best params:
		n_estimators: 1000
		learning_rate: 2.018611900594037
		num_leaves: 1220
		max_depth: 5
		lambda_l1: 0
		lambda_l2: 20
		bagging_fraction: 0.5
		bagging_freq: 1


In [18]:
from sklearn.model_selection import train_test_split
x_train, x_test, y_train, y_test = train_test_split(X, y, test_size=0.15)

In [19]:
import lightgbm as lgbm

params={   
                                  'objective':'binary',
'num_boost_round': 10000,
    'learning_rate':1.1228854903210768,
 #   'num_leaves': 980,
    'max_depth': 5,
 'min_data_in_leaf': 21,
    #'lambda_l1': 0,
    #'lambda_l2': 5,
   
    'bagging_fraction': 0.9,
    'bagging_freq': 1,
    #'feature_fraction': 0.7
}

lgbm_model=lgbm.LGBMClassifier(params)
lgbm_model.n_estimators=10000
lgbm_model

LGBMClassifier(boosting_type={'bagging_fraction': 0.9, 'bagging_freq': 1,
                              'learning_rate': 1.1228854903210768,
                              'max_depth': 5, 'min_data_in_leaf': 21,
                              'num_boost_round': 10000, 'objective': 'binary'},
               n_estimators=10000)

In [20]:
#lgbm_model.fit(x_train,y_train)

In [21]:
#pred=lgbm_model.predict_proba(x_test)

In [22]:
#pred

In [23]:
#competition_log_loss(pred[1],y_test)

In [24]:
#pred=lgbm_model.predict_proba(val)

In [25]:
#pred